In [0]:
if 'dbutils' in locals():
    dbutils.library.restartPython()

!python --version

Python 3.11.0rc1


In [0]:
%load_ext autoreload
%autoreload 2

In [0]:
import os
import sys
from pathlib import Path

workding_dir = str(Path.cwd().parent)
os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /Workspace/Users/donghao.huang@mastercard.com/llm-finetuning


In [0]:
need_to_setup_env = False
need_to_setup_env

False

In [0]:
if need_to_setup_env:
    %pip config set global.index-url https://artifacts.forge.mastercard.com/artifactory/api/pypi/python/simple
    %pip install tf-keras
    %pip install -q --upgrade accelerate einops xformers torchvision
    %pip install -r requirements.txt
    !cd ../LLaMA-Factory && pip install -e .[torch,bitsandbytes] && FLASH_ATTENTION_FORCE_BUILD=TRUE pip install --upgrade flash-attn

In [0]:
os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /Workspace/Users/donghao.huang@mastercard.com/llm-finetuning


In [0]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /Workspace/Users/donghao.huang@mastercard.com/llm-finetuning/.env


True

In [0]:
import os

model_name = os.getenv("MODEL_NAME")
token = os.getenv("HF_TOKEN") or None
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
local_model = os.getenv("LOCAL_MODEL")
hub_model = os.getenv("HUB_MODEL")
num_train_epochs = int(os.getenv("NUM_TRAIN_EPOCHS") or 0)
data_path = os.getenv("DATA_PATH")
results_path = os.getenv("RESULTS_PATH")

max_seq_length = 2048  # Choose any! We auto support RoPE Scaling internally!
dtype = (
    None  # None for auto detection. Float16 for Tesla T4, V100, Bfloat16 for Ampere+
)

model_name, load_in_4bit, local_model, hub_model, max_seq_length, num_train_epochs, dtype, data_path, results_path, os.getenv("DISABLE_MLFLOW_INTEGRATION"), os.getenv("WANDB_DISABLED")

('unsloth/Qwen2-1.5B-Instruct',
 True,
 None,
 None,
 2048,
 10,
 None,
 'datasets/mac/mac.tsv',
 'results/mac-results_lf-r3.csv',
 'TRUE',
 'true')

In [0]:
!nvidia-smi

Sat Jul  6 05:25:48 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.54.03              Driver Version: 535.54.03    CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  Tesla T4                       Off | 00000001:00:00.0 Off |                    0 |
| N/A   63C    P8              11W /  70W |      2MiB / 15360MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

In [0]:
%%time
!python --version
!pip show flash-attn

Python 3.11.0rc1
Name: flash-attn
Version: 2.5.9.post1
Summary: Flash Attention: Fast and Memory-Efficient Exact Attention
Home-page: https://github.com/Dao-AILab/flash-attention
Author: Tri Dao
Author-email: trid@cs.stanford.edu
License: 
Location: /local_disk0/.ephemeral_nfs/envs/pythonEnv-40f92d71-6c52-44a3-a1ef-62cdea633f68/lib/python3.11/site-packages
Requires: einops, torch
Required-by: 
CPU times: user 10.1 ms, sys: 14.5 ms, total: 24.6 ms
Wall time: 4.25 s


In [0]:
%%time

!./scripts/tune-lf.sh config/llama3_8b_lora_sft.yaml

Current Directory:
/Workspace/Users/donghao.huang@mastercard.com/llm-finetuning/llama-factory
config/llama3_8b_lora_sft.yaml:
 {
  "model_name_or_path": "gradientai/Llama-3-8B-Instruct-Gradient-1048k",
  "stage": "sft",
  "do_train": true,
  "finetuning_type": "lora",
  "lora_target": "all",
  "quantization_bit": 4,
  "loraplus_lr_ratio": 16.0,
  "dataset": "alpaca_mac",
  "template": "llama3",
  "cutoff_len": 1024,
  "max_samples": 4528,
  "overwrite_cache": true,
  "preprocessing_num_workers": 16,
  "output_dir": "/Workspace/Users/donghao.huang@mastercard.com/lf-saves/llama3-8b/lora/sft/",
  "logging_steps": 10,
  "save_steps": 560,
  "plot_loss": true,
  "overwrite_output_dir": true,
  "per_device_train_batch_size": 1,
  "gradient_accumulation_steps": 8,
  "learning_rate": 0.0001,
  "num_train_epochs": 6.0,
  "lr_scheduler_type": "cosine",
  "warmup_ratio": 0.1,
  "bf16": true,
  "ddp_timeout": 180000000,
  "val_size": 0.01,
  "per_device_eval_batch_size": 1,
  "eval_strategy": "ste

In [0]:
def evaluate_model_all_epochs(model_name, num_train_epochs, adapter_path_base):
    os.environ["MODEL_NAME"] = model_name 
    for i in range(num_train_epochs + 1):
        print(f"Epoch {i}")
        if i == 0:
            os.unsetenv("ADAPTER_NAME_OR_PATH")
        else:
            adapter_path = f"{adapter_path_base}/checkpoint-{560 * i}"
            os.environ["ADAPTER_NAME_OR_PATH"] = adapter_path
            
        !python llm_toolkit/eval_lf.py

com.databricks.backend.common.rpc.CommandCancelledException
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:429)
	at com.databricks.spark.chauffeur.ChauffeurState.cancelExecution(ChauffeurState.scala:1225)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:958)
	at com.databricks.logging.UsageLogging.$anonfun$recordOperation$1(UsageLogging.scala:525)
	at com.databricks.logging.UsageLogging.executeThunkAndCaptureResultTags$1(UsageLogging.scala:629)
	at com.databricks.logging.UsageLogging.$anonfun$recordOperationWithResultTags$4(UsageLogging.scala:647)
	at com.databricks.logging.AttributionContextTracing.$anonfun$withAttributionContext$1(AttributionContextTracing.scala:48)
	at com.databricks.logging.AttributionContext$.$anonfun$withValue$1(AttributionContext.scala:244)
	at scala.util.DynamicVariable.withValue(DynamicVariable.scala:62)
	at com.databricks.logging.AttributionContext$.withValue(AttributionContext.scala:

In [0]:
%%time

evaluate_model_all_epochs("gradientai/Llama-3-8B-Instruct-Gradient-1048k", num_train_epochs, "/Workspace/Users/donghao.huang@mastercard.com/lf-saves/llama3-8b/lora/sft")

com.databricks.backend.common.rpc.CommandCancelledException
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:429)
	at com.databricks.spark.chauffeur.ChauffeurState.cancelExecution(ChauffeurState.scala:1225)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:958)
	at com.databricks.logging.UsageLogging.$anonfun$recordOperation$1(UsageLogging.scala:525)
	at com.databricks.logging.UsageLogging.executeThunkAndCaptureResultTags$1(UsageLogging.scala:629)
	at com.databricks.logging.UsageLogging.$anonfun$recordOperationWithResultTags$4(UsageLogging.scala:647)
	at com.databricks.logging.AttributionContextTracing.$anonfun$withAttributionContext$1(AttributionContextTracing.scala:48)
	at com.databricks.logging.AttributionContext$.$anonfun$withValue$1(AttributionContext.scala:244)
	at scala.util.DynamicVariable.withValue(DynamicVariable.scala:62)
	at com.databricks.logging.AttributionContext$.withValue(AttributionContext.scala: